In [3]:
#Exercise 3:

#!/usr/bin/env python
# coding: utf-8

# In[2]:


#!/usr/bin/env python3
# -*- coding: utf-8 -*-
import pandas as pd;
from scipy.stats import zscore
import torch as torch;
import numpy as np;
from sklearn.model_selection import train_test_split
np.random.seed(42)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#read in the dataset, convert to numpy
dfData = pd.read_csv(r'C:\Users\Yoges\Desktop\Machine Learning\iris.csv')
np_x=dfData[list(dfData.columns)[0:-1]].apply(zscore).to_numpy();
np_y = pd.get_dummies(dfData['variety']).to_numpy();
n_classes = 3;

x_train, x_test, y_train, y_test = train_test_split(np_x, np_y, test_size=0.20, random_state=42)
n_features = x_train.shape[1];


# reshape training and testing data
# training data
x_train = x_train.astype(dtype='float64')
y_train = y_train.astype(dtype='float64')

# testing data
x_test = x_test.astype(dtype='float64')
y_test = y_test.astype(dtype='float64')

n_train = x_train.shape[0]

#define pytorch linear binary classifier
# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_train=torch.tensor(x_train,requires_grad=False,device=device);
t_y_train=torch.tensor(y_train,requires_grad=False,device=device);


t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);


#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)

# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.001;
optimizer = torch.optim.SGD([W,b],lr=learning_rate)
#optimizer = torch.optim.Adam([W,b],lr=learning_rate)

batch_size=32;
n_epochs = 10000;

for i in range(n_epochs):    
    
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);
        
        # clear previous gradient calculations
        optimizer.zero_grad();
    
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );
    
    
        #calculate gradients of risk w.r.t. W,b and propagate them back
        risk.backward();
        # use the gradient to change W, b
        optimizer.step();
        
        batch_risk=risk.item();
        # calculate accuracy (on the training set!)
        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(activations.detach().cpu().numpy(),axis=1)
        accuracy = np.count_nonzero(true_class == pred_class)/pred_class.shape[0];
        error = 1.0 - accuracy;
        
    # after all the batches in this epoch are done, we calculate test set risk and accuracy
    with (torch.no_grad()):
            linear_predictions = torch.matmul(t_x_test,W)+b
            activations =  torch.exp(linear_predictions);
    
            #Passing through softmax
            sum_activations = torch.sum(activations,dim=1,keepdim=True)
            test_normalized_activations = torch.div(activations, sum_activations);
            cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
            test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
            test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
            test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
            test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
            test_error = 1.0 - test_accuracy;

    
    
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)
    
    #print (t_x_test.shape,test_normalized_activations.shape , t_y_test.shape)


0 1.1022649689772037 1.103005778540273 0.20833333333333334 0.3
1 1.0986919826805137 1.099019747659534 0.2916666666666667 0.36666666666666664
2 1.0951448117605946 1.0950631736231267 0.4583333333333333 0.5666666666666667
3 1.0916232728625008 1.0911358466494747 0.5833333333333334 0.7
4 1.0881271830572785 1.0872375573527528 0.6666666666666666 0.8
5 1.0846563598586407 1.0833680967709094 0.7916666666666666 0.9
6 1.0812106212555825 1.079527256396195 0.7916666666666666 0.9
7 1.0777897857165146 1.0757148282022257 0.7916666666666666 0.9
8 1.0743936722200056 1.0719306046722257 0.7916666666666666 0.9
9 1.0710221002831866 1.068174378822094 0.8333333333333334 0.8666666666666667
10 1.067674889955765 1.0644459442329572 0.8333333333333334 0.8666666666666667
11 1.0643518618674983 1.0607450950729935 0.8333333333333334 0.8666666666666667
12 1.0610528372268349 1.0570716261169484 0.8333333333333334 0.8666666666666667
13 1.0577776378377841 1.0534253327788141 0.8333333333333334 0.8666666666666667
14 1.0545260

119 0.8139717019420436 0.7844938719801554 0.8333333333333334 0.8666666666666667
120 0.8123959888196867 0.7827773897774011 0.8333333333333334 0.8666666666666667
121 0.8108300340507709 0.7810719019352526 0.8333333333333334 0.8666666666666667
122 0.8092737559235644 0.7793773147578513 0.8333333333333334 0.8666666666666667
123 0.807727073434013 0.7776935353883159 0.8333333333333334 0.8666666666666667
124 0.8061899062519912 0.7760204718169985 0.8333333333333334 0.8666666666666667
125 0.8046621749938484 0.7743580329207399 0.8333333333333334 0.8666666666666667
126 0.8031438006938947 0.7727061283930188 0.8333333333333334 0.8666666666666667
127 0.8016347054242998 0.77106466874462 0.8333333333333334 0.8666666666666667
128 0.8001348117191981 0.7694335653376643 0.8333333333333334 0.8666666666666667
129 0.79864404292509 0.7678127303651963 0.8333333333333334 0.8666666666666667
130 0.7971623231356647 0.766202076803793 0.8333333333333334 0.8666666666666667
131 0.7956895771496532 0.7646015184580816 0.83

227 0.68687268475133 0.647411801755867 0.8333333333333334 0.8666666666666667
228 0.6860018135582638 0.6464834732079496 0.8333333333333334 0.8666666666666667
229 0.6851351082961415 0.6455597506559585 0.8333333333333334 0.8666666666666667
230 0.6842725389013132 0.6446406000185773 0.875 0.8666666666666667
231 0.6834140755837165 0.6437259875311957 0.875 0.8666666666666667
232 0.6825596886751795 0.6428158797379037 0.875 0.8666666666666667
233 0.6817093493966305 0.6419102434835134 0.875 0.8666666666666667
234 0.6808630284148949 0.6410090459038076 0.875 0.8666666666666667
235 0.6800206970833838 0.6401122544296098 0.875 0.8666666666666667
236 0.6791823271127484 0.6392198368169377 0.875 0.8666666666666667
237 0.6783478904156434 0.6383317610828588 0.875 0.8666666666666667
238 0.6775173587261522 0.6374479955330344 0.875 0.8666666666666667
239 0.6766907046059556 0.6365685087805008 0.875 0.8666666666666667
240 0.6758679005222911 0.6356932696811799 0.875 0.8666666666666667
241 0.6750489194204133 0.6

366 0.5957596743350901 0.551217302933098 0.875 0.8666666666666667
367 0.5952666817293917 0.5507018796309125 0.875 0.8666666666666667
368 0.5947754032048587 0.550188299486756 0.875 0.8666666666666667
369 0.5942858289302809 0.5496765517915722 0.875 0.8666666666666667
370 0.5937979500359543 0.5491666259841758 0.875 0.8666666666666667
371 0.5933117565587394 0.5486585115365518 0.875 0.8666666666666667
372 0.5928272393615915 0.5481521980316384 0.875 0.8666666666666667
373 0.5923443893361822 0.5476476751725712 0.875 0.8666666666666667
374 0.5918631966699944 0.5471449327026012 0.875 0.8666666666666667
375 0.5913836527971069 0.546643960446417 0.875 0.8666666666666667
376 0.5909057481766347 0.546144748232664 0.875 0.8666666666666667
377 0.5904294741440178 0.5456472861329112 0.875 0.8666666666666667
378 0.58995482154102 0.5451515641674436 0.875 0.8666666666666667
379 0.5894817812386158 0.5446575723586075 0.875 0.8666666666666667
380 0.5890103446339868 0.5441653011244302 0.875 0.8666666666666667
3

537 0.5303951639740039 0.4832661101409606 0.875 0.9
538 0.530097818042481 0.48295841563615866 0.875 0.9
539 0.529801217999392 0.48265150216690794 0.875 0.9
540 0.5295053609889934 0.48234536617780643 0.875 0.9
541 0.5292102434842151 0.482040004267492 0.875 0.9
542 0.5289158630991834 0.4817354128743498 0.875 0.9
543 0.5286222165019476 0.48143158895919574 0.875 0.9
544 0.5283293005262228 0.48112852908929116 0.875 0.9
545 0.5280371121641309 0.4808262300462628 0.875 0.9
546 0.5277456481943376 0.480524688539692 0.875 0.9
547 0.527454905301025 0.48022390161216133 0.875 0.9
548 0.5271648811309014 0.4799238657566421 0.875 0.9
549 0.5268755726028743 0.4796245776831833 0.875 0.9
550 0.5265869763982969 0.4793260341773998 0.875 0.9
551 0.5262990899936888 0.4790282322650102 0.875 0.9
552 0.5260119100510535 0.4787311687569468 0.875 0.9
553 0.5257254337189027 0.47843484049497614 0.875 0.9
554 0.5254396581449435 0.47813924463685414 0.875 0.9
555 0.52515458117536 0.477844377744504 0.875 0.9
556 0.524870

...

9383 0.19531890699602894 0.1629160964014177 1.0 0.9666666666666667
9384 0.19530836669780535 0.1629074519404283 1.0 0.9666666666666667
9385 0.19529782811328253 0.16289880841782517 1.0 0.9666666666666667
9386 0.19528729124167077 0.16289016583345065 1.0 0.9666666666666667
9387 0.19527675216703952 0.1628815279596245 1.0 0.9666666666666667
9388 0.19526621480984255 0.16287289102280228 1.0 0.9666666666666667
9389 0.1952556768733341 0.16286425705823723 1.0 0.9666666666666667
9390 0.19524514065613577 0.1628556240298691 1.0 0.9666666666666667
9391 0.19523460615744936 0.1628469919375408 1.0 0.9666666666666667
9392 0.19522407337647796 0.16283836078109531 1.0 0.9666666666666667
9393 0.1952135400181991 0.1628297325954073 1.0 0.9666666666666667
9394 0.1952030083795057 0.16282110534479566 1.0 0.9666666666666667
9395 0.19519247845959856 0.1628124790291037 1.0 0.9666666666666667
9396 0.19518195025767918 0.16280385364817476 1.0 0.9666666666666667
9397 0.1951714237729498 0.1627952292018523 1.0 0.966666666

9528 0.193804671626123 0.16167580502655265 1.0 0.9666666666666667
9529 0.19379433316194164 0.16166733607320433 1.0 0.9666666666666667
9530 0.19378399636574387 0.16165886795020812 1.0 0.9666666666666667
9531 0.19377366140225258 0.16165040073322706 1.0 0.9666666666666667
9532 0.19376332581394184 0.16164193645409816 1.0 0.9666666666666667
9533 0.19375298797751547 0.1616334768403654 1.0 0.9666666666666667
9534 0.19374265181528458 0.16162501813076566 1.0 0.9666666666666667
9535 0.19373231732647245 0.16161656032515317 1.0 0.9666666666666667
9536 0.1937219845103034 0.16160810342338205 1.0 0.9666666666666667
9537 0.19371165107668176 0.16159964945687824 1.0 0.9666666666666667
9538 0.19370131931758586 0.16159119639341732 1.0 0.9666666666666667
9539 0.19369098923223785 0.16158274423285382 1.0 0.9666666666666667
9540 0.19368066081986043 0.16157429297504222 1.0 0.9666666666666667
9541 0.19367033407967724 0.16156584261983717 1.0 0.9666666666666667
9542 0.19366000917620488 0.16155739309122547 1.0 0.9

9681 0.19223821946996345 0.1603941717225806 1.0 0.9666666666666667
9682 0.19222808090382185 0.16038588831125639 1.0 0.9666666666666667
9683 0.19221794413181392 0.16037760569494589 1.0 0.9666666666666667
9684 0.1922078089904015 0.16036932395063824 1.0 0.9666666666666667
9685 0.1921976754788275 0.16036104307819882 1.0 0.9666666666666667
9686 0.1921875435963356 0.1603527630774927 1.0 0.9666666666666667
9687 0.19217741334216995 0.16034448394838519 1.0 0.9666666666666667
9688 0.19216728471557556 0.16033620569074175 1.0 0.9666666666666667
9689 0.19215715771579822 0.1603279283044277 1.0 0.9666666666666667
9690 0.19214703234208427 0.16031965178930865 1.0 0.9666666666666667
9691 0.19213690859368093 0.16031137614524998 1.0 0.9666666666666667
9692 0.19212678646983614 0.1603031013721175 1.0 0.9666666666666667
9693 0.1921166659697983 0.16029482746977672 1.0 0.9666666666666667
9694 0.19210654709281683 0.16028655443809342 1.0 0.9666666666666667
9695 0.19209642983814165 0.16027828227693344 1.0 0.96666

9821 0.19083224329623114 0.15924504534703568 1.0 0.9666666666666667
9822 0.190822293745304 0.15923691602021176 1.0 0.9666666666666667
9823 0.19081234577652914 0.15922878753844893 1.0 0.9666666666666667
9824 0.19080239938917845 0.15922065990162165 1.0 0.9666666666666667
9825 0.19079245230131445 0.15921253513426242 1.0 0.9666666666666667
9826 0.1907825067967935 0.15920441121105194 1.0 0.9666666666666667
9827 0.19077256287488556 0.1591962881318649 1.0 0.9666666666666667
9828 0.19076261825529653 0.15918816792085452 1.0 0.9666666666666667
9829 0.19075267537998997 0.15918004847478404 1.0 0.9666666666666667
9830 0.1907427340882801 0.1591719298718471 1.0 0.9666666666666667
9831 0.19073279437943558 0.1591638121119188 1.0 0.9666666666666667
9832 0.1907228562527259 0.15915569519487416 1.0 0.9666666666666667
9833 0.19071291578735353 0.1591475828555698 1.0 0.9666666666666667
9834 0.19070297690861057 0.15913947135791245 1.0 0.9666666666666667
9835 0.19069303961576112 0.15913136070177764 1.0 0.966666

9960 0.1894613353519825 0.15812588577409242 1.0 0.9666666666666667
9961 0.18945156098811258 0.1581179117097011 1.0 0.9666666666666667
9962 0.18944178816985424 0.15810993846293217 1.0 0.9666666666666667
9963 0.18943201689649514 0.158101966033669 1.0 0.9666666666666667
9964 0.18942224716732334 0.1580939944217953 1.0 0.9666666666666667
9965 0.18941247898162775 0.1580860236271947 1.0 0.9666666666666667
9966 0.18940271233869801 0.15807805364975072 1.0 0.9666666666666667
9967 0.1893929472378243 0.1580700844893472 1.0 0.9666666666666667
9968 0.18938318367829754 0.15806211614586793 1.0 0.9666666666666667
9969 0.18937342165940918 0.15805414861919667 1.0 0.9666666666666667
9970 0.18936366118045136 0.1580461819092172 1.0 0.9666666666666667
9971 0.18935390224071721 0.15803821601581355 1.0 0.9666666666666667
9972 0.1893441448395002 0.15803025093886966 1.0 0.9666666666666667
9973 0.18933438897609448 0.15802228667826942 1.0 0.9666666666666667
9974 0.189324634649795 0.158014323233897 1.0 0.96666666666

In [11]:
#Exercise 3:

#!/usr/bin/env python
# coding: utf-8

# In[2]:


#!/usr/bin/env python3
# -*- coding: utf-8 -*-
import pandas as pd;
from scipy.stats import zscore
import torch as torch;
import numpy as np;
from sklearn.model_selection import train_test_split
np.random.seed(42)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#read in the dataset, convert to numpy
dfData = pd.read_csv(r'C:\Users\Yoges\Desktop\Machine Learning\iris.csv')
np_x=dfData[list(dfData.columns)[0:-1]].apply(zscore).to_numpy();
np_y = pd.get_dummies(dfData['variety']).to_numpy();
n_classes = 3;

x_train, x_test, y_train, y_test = train_test_split(np_x, np_y, test_size=0.20, random_state=42)
n_features = x_train.shape[1];


# reshape training and testing data
# training data
x_train = x_train.astype(dtype='float64')
y_train = y_train.astype(dtype='float64')

# testing data
x_test = x_test.astype(dtype='float64')
y_test = y_test.astype(dtype='float64')

n_train = x_train.shape[0]

#define pytorch linear binary classifier
# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_train=torch.tensor(x_train,requires_grad=False,device=device);
t_y_train=torch.tensor(y_train,requires_grad=False,device=device);


t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);


#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)

# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.001;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)

batch_size=32;
n_epochs = 10000;

for i in range(n_epochs):    
    
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);
        
        # clear previous gradient calculations
        optimizer.zero_grad();
    
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );
    
    
        #calculate gradients of risk w.r.t. W,b and propagate them back
        risk.backward();
        # use the gradient to change W, b
        optimizer.step();
        
        batch_risk=risk.item();
        # calculate accuracy (on the training set!)
        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(activations.detach().cpu().numpy(),axis=1)
        accuracy = np.count_nonzero(true_class == pred_class)/pred_class.shape[0];
        error = 1.0 - accuracy;
        
    # after all the batches in this epoch are done, we calculate test set risk and accuracy
    with (torch.no_grad()):
            linear_predictions = torch.matmul(t_x_test,W)+b
            activations =  torch.exp(linear_predictions);
    
            #Passing through softmax
            sum_activations = torch.sum(activations,dim=1,keepdim=True)
            test_normalized_activations = torch.div(activations, sum_activations);
            cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
            test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
            test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
            test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
            test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
            test_error = 1.0 - test_accuracy;

    
    
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)
    
    #print (t_x_test.shape,test_normalized_activations.shape , t_y_test.shape)


0 1.0981693403533457 1.0954288196598307 0.4166666666666667 0.5
1 1.0883675409557643 1.0840434553879 0.4583333333333333 0.6
2 1.07859261751147 1.0728168138628933 0.75 0.7666666666666667
3 1.0689105811014337 1.0617520968406613 0.75 0.8
4 1.0593454165737972 1.0508538365325435 0.75 0.8333333333333334
5 1.0499091229098074 1.040125936006991 0.75 0.9
6 1.0406085011020072 1.0295712983424508 0.7916666666666666 0.9333333333333333
7 1.0314474706209467 1.019191779078716 0.7916666666666666 0.9333333333333333
8 1.02242810212571 1.0089882552502072 0.7916666666666666 0.9333333333333333
9 1.01355118255559 0.9989607445199639 0.8333333333333334 0.9333333333333333
10 1.0048165744068618 0.9891085417941049 0.8333333333333334 0.9333333333333333
11 0.9962234670542176 0.9794303547970333 0.8333333333333334 0.9333333333333333
12 0.9877705611340725 0.9699244276582369 0.8333333333333334 0.9333333333333333
13 0.9794562071068841 0.9605886480432114 0.8333333333333334 0.9
14 0.9712785093181956 0.9514206362919843 0.833

148 0.5008690977581839 0.449245607900745 0.9166666666666666 0.9333333333333333
149 0.499477790552525 0.4477979743185288 0.9166666666666666 0.9333333333333333
150 0.49809871869665495 0.44636337959139566 0.9166666666666666 0.9333333333333333
151 0.4967316933656845 0.4449416352362088 0.9166666666666666 0.9333333333333333
152 0.4953765286488306 0.44353255567958727 0.9166666666666666 0.9333333333333333
153 0.4940330430735124 0.442135958699759 0.9166666666666666 0.9333333333333333
154 0.4927010592339955 0.44075166568244145 0.9166666666666666 0.9333333333333333
155 0.49138040125473975 0.4393795009733408 0.9166666666666666 0.9333333333333333
156 0.49007089714342494 0.438019292514345 0.9166666666666666 0.9333333333333333
157 0.4887723798051539 0.43667087123476017 0.9166666666666666 0.9333333333333333
158 0.4874846826614343 0.4353340706128062 0.9166666666666666 0.9333333333333333
159 0.486207642836733 0.43400872759395254 0.9166666666666666 0.9333333333333333
160 0.4849411022386802 0.432694682030

256 0.3958408714982335 0.3423416861426964 0.9166666666666666 0.9333333333333333
257 0.3951371061026114 0.34165302172712714 0.9166666666666666 0.9333333333333333
258 0.39443641505227944 0.3409678646125845 0.9166666666666666 0.9333333333333333
259 0.393738767724451 0.34028617830140806 0.9166666666666666 0.9333333333333333
260 0.3930441347767215 0.33960792841640514 0.9166666666666666 0.9333333333333333
261 0.3923524854189679 0.338933080983267 0.9166666666666666 0.9333333333333333
262 0.3916637909062786 0.33826160075652845 0.9166666666666666 0.9333333333333333
263 0.3909780212755944 0.33759345519944833 0.9166666666666666 0.9333333333333333
264 0.39029514816745764 0.33692861062629903 0.9166666666666666 0.9666666666666667
265 0.3896151421645369 0.33626703449118694 0.9166666666666666 0.9666666666666667
266 0.3889379778904163 0.3356086941483893 0.9166666666666666 0.9666666666666667
267 0.38826362538720094 0.3349535583327807 0.9166666666666666 0.9666666666666667
268 0.38759205825628906 0.334301

368 0.3311188455782765 0.2811046349313539 0.9166666666666666 0.9666666666666667
369 0.33063639246876675 0.28066290650942016 0.9166666666666666 0.9666666666666667
370 0.3301552138699874 0.28022253359105054 0.9166666666666666 0.9666666666666667
371 0.32967530690482405 0.27978350600719576 0.9166666666666666 0.9666666666666667
372 0.32919665961757366 0.2793458142475806 0.9166666666666666 0.9666666666666667
373 0.3287192678480025 0.2789094507947497 0.9166666666666666 0.9666666666666667
374 0.32824312427604496 0.2784744035080507 0.9166666666666666 0.9666666666666667
375 0.327768218332031 0.2780406669164162 0.9166666666666666 0.9666666666666667
376 0.32729454899746246 0.2776082299230589 0.9166666666666666 0.9666666666666667
377 0.3268221029392357 0.27717708650751444 0.9166666666666666 0.9666666666666667
378 0.3263508736769201 0.2767472261721436 0.9166666666666666 0.9666666666666667
379 0.3258808558663948 0.27631864126228023 0.9166666666666666 0.9666666666666667
380 0.32541204640818 0.27589132

478 0.28443643103049576 0.23910075727037178 0.9166666666666666 0.9666666666666667
479 0.28406186335206385 0.2387688565305964 0.9166666666666666 0.9666666666666667
480 0.2836880579405806 0.23843770265946715 0.9166666666666666 0.9666666666666667
481 0.2833150184576723 0.23810729118280355 0.9166666666666666 0.9666666666666667
482 0.282942735138442 0.23777762207717626 0.9166666666666666 0.9666666666666667
483 0.28257120663086993 0.2374486917509245 0.9166666666666666 0.9666666666666667
484 0.28220043200467954 0.2371204963445958 0.9166666666666666 0.9666666666666667
485 0.2818304086399203 0.23679303315788833 0.9166666666666666 0.9666666666666667
486 0.2814611332073165 0.23646630006155356 0.9166666666666666 0.9666666666666667
487 0.28109260201400604 0.2361402929813216 0.9166666666666666 0.9666666666666667
488 0.2807248102872737 0.23581501155193482 0.9166666666666666 0.9666666666666667
489 0.2803577637157922 0.23549044779907172 0.9166666666666666 0.9666666666666667
490 0.27999145192960817 0.23

...

9306 0.020562800463113914 0.030691755933674524 1.0 1.0
9307 0.020561525610045456 0.030690336753135837 1.0 1.0
9308 0.020560251661797802 0.030688917717882156 1.0 1.0
9309 0.020558978607273206 0.030687498833769204 1.0 1.0
9310 0.02055770643556397 0.030686080106534615 1.0 1.0
9311 0.020556435135951266 0.030684661541798792 1.0 1.0
9312 0.020555164697902622 0.030683243145066548 1.0 1.0
9313 0.02055389511106957 0.030681824921728815 1.0 1.0
9314 0.020552626365284824 0.030680406877064432 1.0 1.0
9315 0.02055135845055912 0.03067898901624195 1.0 1.0
9316 0.02055009135707854 0.03067757134432166 1.0 1.0
9317 0.020548825075201307 0.03067615386625737 1.0 1.0
9318 0.020547559595454654 0.03067473658689863 1.0 1.0
9319 0.020546294908531885 0.030673319510992166 1.0 1.0
9320 0.02054503100528938 0.03067190264318411 1.0 1.0
9321 0.02054376787674361 0.030670485988021783 1.0 1.0
9322 0.02054250551406828 0.03066906954995546 1.0 1.0
9323 0.020541243908591328 0.030667653333340116 1.0 1.0
9324 0.0205399830517922

9462 0.020366854480593024 0.030473354263182924 1.0 1.0
9463 0.020365612249155413 0.03047197239189764 1.0 1.0
9464 0.020364370988682625 0.030470590607790574 1.0 1.0
9465 0.02036313068696267 0.030469208917408733 1.0 1.0
9466 0.020361891331911765 0.030467827327207223 1.0 1.0
9467 0.02036065291160126 0.030466445843537204 1.0 1.0
9468 0.020359415414274256 0.030465064472638793 1.0 1.0
9469 0.02035817882835541 0.03046368322063734 1.0 1.0
9470 0.020356943142456257 0.030462302093540956 1.0 1.0
9471 0.020355708345377675 0.03046092109724041 1.0 1.0
9472 0.020354474426110204 0.03045954023750919 1.0 1.0
9473 0.02035324137383322 0.030458159520004646 1.0 1.0
9474 0.020352009177913133 0.030456778950269096 1.0 1.0
9475 0.02035077782790125 0.030455398533731703 1.0 1.0
9476 0.020349547313530954 0.030454018275709822 1.0 1.0
9477 0.020348317624715048 0.030452638181411137 1.0 1.0
9478 0.02034708875154275 0.030451258255935424 1.0 1.0
9479 0.02034586068427672 0.03044987850427639 1.0 1.0
9480 0.020344633413350

9639 0.0201519148532552 0.030232174364783027 1.0 1.0
9640 0.02015072172993006 0.03023083248665408 1.0 1.0
9641 0.02014952936302816 0.030229490775976118 1.0 1.0
9642 0.020148337763071334 0.030228149228768885 1.0 1.0
9643 0.0201471469339356 0.03022680784395536 1.0 1.0
9644 0.020145949502760187 0.03022546757963981 1.0 1.0
9645 0.020144752875016405 0.03022412745419923 1.0 1.0
9646 0.02014355707268856 0.03022278745839731 1.0 1.0
9647 0.020142362107488782 0.03022144758792833 1.0 1.0
9648 0.020141167983661314 0.030220107841752608 1.0 1.0
9649 0.020139967325238463 0.030218769182875846 1.0 1.0
9650 0.020138760155038356 0.030217431596482543 1.0 1.0
9651 0.02013755389829999 0.030216094091979107 1.0 1.0
9652 0.02013634859995553 0.030214756648059074 1.0 1.0
9653 0.020135144285335613 0.03021341925297793 1.0 1.0
9654 0.020133940966763235 0.030212081901339307 1.0 1.0
9655 0.020132738647955423 0.030210744591945757 1.0 1.0
9656 0.020131537326961938 0.030209407326361216 1.0 1.0
9657 0.020130336998125865 

9792 0.019971563578465096 0.030029251215640738 1.0 1.0
9793 0.01997041552936422 0.0300279396109976 1.0 1.0
9794 0.01996926808337233 0.030026628242997146 1.0 1.0
9795 0.019968121234128066 0.030025317114574266 1.0 1.0
9796 0.01996697497537881 0.03002400622859908 1.0 1.0
9797 0.01996582930097882 0.030022695587878068 1.0 1.0
9798 0.019964684204887145 0.03002138519515528 1.0 1.0
9799 0.019963539681165928 0.030020075053113476 1.0 1.0
9800 0.01996239572397839 0.030018765164375318 1.0 1.0
9801 0.01996125232758697 0.030017455531504273 1.0 1.0
9802 0.01996010948635179 0.030016146157005992 1.0 1.0
9803 0.019958967194728502 0.030014837043329155 1.0 1.0
9804 0.019957825447266906 0.030013528192866564 1.0 1.0
9805 0.019956684238609093 0.030012219607956293 1.0 1.0
9806 0.01995554356348775 0.030010911290882642 1.0 1.0
9807 0.0199544034167246 0.03000960415259847 1.0 1.0
9808 0.019953256475331544 0.03000829727351469 1.0 1.0
9809 0.019952110103235117 0.030006990639407607 1.0 1.0
9810 0.019950964317842282 

9944 0.019797735266089612 0.029832482009224347 1.0 1.0
9945 0.019796615631129204 0.029831202752576506 1.0 1.0
9946 0.01979549663999946 0.02982992369087263 1.0 1.0
9947 0.019794370990309337 0.029828645682061537 1.0 1.0
9948 0.01979324600491341 0.029827367849614306 1.0 1.0
9949 0.019792121704548544 0.02982609018525274 1.0 1.0
9950 0.01979099810016818 0.02982481268485376 1.0 1.0
9951 0.01978986790287849 0.029823537060796438 1.0 1.0
9952 0.019788731159902127 0.029822261561626966 1.0 1.0
9953 0.019787595228125555 0.029820986161368395 1.0 1.0
9954 0.01978646014306402 0.029819710844748926 1.0 1.0
9955 0.01978532592442664 0.029818435603622857 1.0 1.0
9956 0.01978419258143934 0.029817161293531964 1.0 1.0
9957 0.01978305283729652 0.02981588704248977 1.0 1.0
9958 0.019781914019439236 0.029814612836237434 1.0 1.0
9959 0.01978077614474887 0.02981333866756053 1.0 1.0
9960 0.01977963922015197 0.02981206453391313 1.0 1.0
9961 0.019778503246004397 0.029810790435828415 1.0 1.0
9962 0.019777368218349554 

In [6]:
#Exercise 3:

#!/usr/bin/env python
# coding: utf-8

# In[2]:


#!/usr/bin/env python3
# -*- coding: utf-8 -*-
import pandas as pd;
from scipy.stats import zscore
import torch as torch;
import numpy as np;
from sklearn.model_selection import train_test_split
np.random.seed(42)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#read in the dataset, convert to numpy
dfData = pd.read_csv(r'C:\Users\Yoges\Desktop\Machine Learning\iris.csv')
np_x=dfData[list(dfData.columns)[0:-1]].apply(zscore).to_numpy();
np_y = pd.get_dummies(dfData['variety']).to_numpy();
n_classes = 3;

x_train, x_test, y_train, y_test = train_test_split(np_x, np_y, test_size=0.20, random_state=42)
n_features = x_train.shape[1];


# reshape training and testing data
# training data
x_train = x_train.astype(dtype='float64')
y_train = y_train.astype(dtype='float64')

# testing data
x_test = x_test.astype(dtype='float64')
y_test = y_test.astype(dtype='float64')

n_train = x_train.shape[0]

#define pytorch linear binary classifier
# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_train=torch.tensor(x_train,requires_grad=False,device=device);
t_y_train=torch.tensor(y_train,requires_grad=False,device=device);


t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);


#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)

# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.01;
optimizer = torch.optim.SGD([W,b],lr=learning_rate)
#optimizer = torch.optim.Adam([W,b],lr=learning_rate)

batch_size=64;
n_epochs = 10000;

for i in range(n_epochs):    
    
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);
        
        # clear previous gradient calculations
        optimizer.zero_grad();
    
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );
    
    
        #calculate gradients of risk w.r.t. W,b and propagate them back
        risk.backward();
        # use the gradient to change W, b
        optimizer.step();
        
        batch_risk=risk.item();
        # calculate accuracy (on the training set!)
        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(activations.detach().cpu().numpy(),axis=1)
        accuracy = np.count_nonzero(true_class == pred_class)/pred_class.shape[0];
        error = 1.0 - accuracy;
        
    # after all the batches in this epoch are done, we calculate test set risk and accuracy
    with (torch.no_grad()):
            linear_predictions = torch.matmul(t_x_test,W)+b
            activations =  torch.exp(linear_predictions);
    
            #Passing through softmax
            sum_activations = torch.sum(activations,dim=1,keepdim=True)
            test_normalized_activations = torch.div(activations, sum_activations);
            cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
            test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
            test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
            test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
            test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
            test_error = 1.0 - test_accuracy;

    
    
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)
    
    #print (t_x_test.shape,test_normalized_activations.shape , t_y_test.shape)


0 1.0973091343560284 1.087144882613436 0.375 0.8666666666666667
1 1.0796703597421848 1.0679971014162812 0.75 0.9
2 1.0626739882965817 1.0495518307711804 0.7678571428571429 0.8666666666666667
3 1.0462969096284047 1.03178312402778 0.7857142857142857 0.8666666666666667
4 1.0305163359539733 1.0146654672722604 0.7857142857142857 0.8666666666666667
5 1.0153098643791316 0.9981738463424163 0.7857142857142857 0.8666666666666667
6 1.0006555314389463 0.9822838039662259 0.7857142857142857 0.8666666666666667
7 0.986531860162893 0.9669714875401024 0.7857142857142857 0.8666666666666667
8 0.9729178998340513 0.9522136880812795 0.7857142857142857 0.8666666666666667
9 0.9597932588608292 0.9379878710267534 0.7857142857142857 0.8666666666666667
10 0.9471381311450369 0.9242721995855608 0.7857142857142857 0.8666666666666667
11 0.9349333163350393 0.9110455512372617 0.7857142857142857 0.8666666666666667
12 0.9231602345592196 0.8982875281201449 0.7857142857142857 0.8666666666666667
13 0.9118009360116647 0.88597

146 0.49330039305589163 0.43424418914795443 0.8214285714285714 0.9
147 0.4923599860183195 0.4332436095602048 0.8214285714285714 0.9
148 0.4914280710139069 0.4322521998663734 0.8214285714285714 0.9
149 0.49050451320517435 0.43126981293805833 0.8214285714285714 0.9
150 0.48958917853301376 0.4302963051209581 0.8214285714285714 0.9
151 0.48868193820765626 0.4293315365399953 0.8214285714285714 0.9
152 0.4877826649449583 0.42837536928489145 0.8214285714285714 0.9
153 0.486891234597525 0.42742766927397374 0.8214285714285714 0.9
154 0.4860075264333301 0.42648830512924824 0.8214285714285714 0.9
155 0.48513142038227336 0.42555714829938823 0.8214285714285714 0.9
156 0.4842628005872725 0.4246340726234211 0.8214285714285714 0.9
157 0.48340155207782215 0.42371895463102177 0.8214285714285714 0.9
158 0.48254756426012335 0.4228116745758545 0.8214285714285714 0.9
159 0.4817007273267836 0.4219121141742304 0.8214285714285714 0.9
160 0.4808609356194829 0.4210201587054091 0.8214285714285714 0.9
161 0.480028

308 0.40123472547717765 0.33740004725910355 0.875 0.9333333333333333
309 0.4008724090383436 0.33702707585813463 0.875 0.9333333333333333
310 0.40051148413154697 0.33665564937444753 0.875 0.9333333333333333
311 0.4001519411898882 0.33628575554832263 0.875 0.9333333333333333
312 0.39979376901809144 0.3359173831675637 0.875 0.9333333333333333
313 0.3994369558236688 0.3355505180268544 0.875 0.9333333333333333
314 0.3990814909915637 0.3351851508926893 0.875 0.9333333333333333
315 0.39872736403115727 0.3348212693468101 0.875 0.9333333333333333
316 0.39837456528790494 0.3344588622110881 0.875 0.9333333333333333
317 0.3980230828211034 0.33409791850809384 0.875 0.9333333333333333
318 0.3976729082611789 0.3337384269726163 0.875 0.9333333333333333
319 0.3973240290392516 0.33338037667162784 0.875 0.9333333333333333
320 0.39697643695172186 0.3330237557915646 0.875 0.9333333333333333
321 0.39663012161358224 0.3326685550022065 0.875 0.9333333333333333
322 0.3962850722750865 0.3323147635821904 0.875 0

465 0.35648128827450754 0.2924172156416275 0.9285714285714286 0.9333333333333333
466 0.3562521190341492 0.2921937149930647 0.9285714285714286 0.9333333333333333
467 0.35602345884580666 0.2919707904902328 0.9285714285714286 0.9333333333333333
468 0.3557953047944595 0.291748439800878 0.9285714285714286 0.9333333333333333
469 0.35556765421267106 0.2915266590756992 0.9285714285714286 0.9333333333333333
470 0.35534050503621095 0.29130544644589756 0.9285714285714286 0.9333333333333333
471 0.3551138548335294 0.29108479913305446 0.9285714285714286 0.9333333333333333
472 0.35488770035160827 0.2908647133525532 0.9285714285714286 0.9333333333333333
473 0.35466204003367163 0.2906451873906312 0.9285714285714286 0.9333333333333333
474 0.3544368708897407 0.2904262175953843 0.9285714285714286 0.9333333333333333
475 0.35421219117355357 0.29020780211046676 0.9285714285714286 0.9333333333333333
476 0.3539879974884591 0.28998993732512657 0.9285714285714286 0.9333333333333333
477 0.3537642885697802 0.28977

613 0.32703571167596246 0.2643873335381165 0.9285714285714286 0.9666666666666667
614 0.32686162282214565 0.26422582596218647 0.9285714285714286 0.9666666666666667
615 0.3266878072002554 0.2640646218365101 0.9285714285714286 0.9666666666666667
616 0.3265142642759941 0.263903719960033 0.9285714285714286 0.9666666666666667
617 0.32634099287196916 0.2637431172587533 0.9285714285714286 0.9666666666666667
618 0.32616799060174423 0.2635828147842766 0.9285714285714286 0.9666666666666667
619 0.3259952583396002 0.26342281135512285 0.9285714285714286 0.9666666666666667
620 0.32582279455470176 0.263263103914327 0.9285714285714286 0.9666666666666667
621 0.3256505979940646 0.2631036934139694 0.9285714285714286 0.9666666666666667
622 0.3254786677851217 0.26294457881065403 0.9285714285714286 0.9666666666666667
623 0.32530700268798535 0.26278575517845526 0.9285714285714286 0.9666666666666667
624 0.32513560150791243 0.26262722524657267 0.9285714285714286 0.9666666666666667
625 0.3249644651431539 0.26246

...

9117 0.08680399526278626 0.07569269663183142 1.0 1.0
9118 0.08679878679150999 0.07568919589627894 1.0 1.0
9119 0.08679357934433041 0.07568569537967382 1.0 1.0
9120 0.08678837292033452 0.0756821950830453 1.0 1.0
9121 0.0867831675186116 0.07567869500741929 1.0 1.0
9122 0.08677796313825295 0.07567519515381856 1.0 1.0
9123 0.08677275977835218 0.07567169552326256 1.0 1.0
9124 0.08676755743800499 0.07566819611676757 1.0 1.0
9125 0.08676235611630931 0.0756646969353467 1.0 1.0
9126 0.08675715581236516 0.0756611979800098 1.0 1.0
9127 0.08675195559391737 0.0756577033016475 1.0 1.0
9128 0.08674675639806535 0.0756542088396348 1.0 1.0
9129 0.0867415582238963 0.07565071459500332 1.0 1.0
9130 0.08673636107049942 0.07564722056878156 1.0 1.0
9131 0.0867311649369663 0.07564372676199478 1.0 1.0
9132 0.08672596982239057 0.07564023317566493 1.0 1.0
9133 0.08672077572586802 0.07563673981081087 1.0 1.0
9134 0.08671558193628859 0.07563325128953652 1.0 1.0
9135 0.08671038916962961 0.07562976298007738 1.0 1.0
9

9305 0.08584114308395951 0.07504517761088367 1.0 1.0
9306 0.08583610772233065 0.07504179001855592 1.0 1.0
9307 0.08583107333142252 0.07503840263444932 1.0 1.0
9308 0.0858260399103841 0.07503501545953642 1.0 1.0
9309 0.08582100745836628 0.07503162849478677 1.0 1.0
9310 0.08581597597452198 0.07502824174116687 1.0 1.0
9311 0.08581094545800616 0.07502485519964021 1.0 1.0
9312 0.08580591590797577 0.07502146887116726 1.0 1.0
9313 0.08580088732358969 0.07501808275670543 1.0 1.0
9314 0.08579585970400887 0.07501469685720924 1.0 1.0
9315 0.08579083304839619 0.07501131117363018 1.0 1.0
9316 0.0857858073559165 0.07500792570691671 1.0 1.0
9317 0.08578078095996086 0.07500454904332665 1.0 1.0
9318 0.08577575553852179 0.07500117257529158 1.0 1.0
9319 0.08577073109073152 0.07499779630381331 1.0 1.0
9320 0.08576570761572425 0.07499442022989035 1.0 1.0
9321 0.08576068511263635 0.07499104435451823 1.0 1.0
9322 0.08575566358060614 0.07498766867868929 1.0 1.0
9323 0.08575064301877408 0.07498429320339287 1.0

9507 0.0848418214359666 0.07437280921591904 1.0 1.0
9508 0.08483696190298758 0.07436953859326119 1.0 1.0
9509 0.08483210329025459 0.07436626816342946 1.0 1.0
9510 0.0848272455969687 0.07436299792735296 1.0 1.0
9511 0.08482238882233291 0.07435972788595786 1.0 1.0
9512 0.08481753296555199 0.07435645804016751 1.0 1.0
9513 0.08481267802583266 0.07435318839090238 1.0 1.0
9514 0.0848078230476873 0.07434992290751646 1.0 1.0
9515 0.08480296899139776 0.07434665761097574 1.0 1.0
9516 0.08479811585615814 0.07434339250222255 1.0 1.0
9517 0.0847932636411644 0.07434012758219616 1.0 1.0
9518 0.08478841234561438 0.07433686285183318 1.0 1.0
9519 0.08478356196870782 0.07433359831206714 1.0 1.0
9520 0.08477871250964637 0.07433033396382868 1.0 1.0
9521 0.08477386396763353 0.07432706980804582 1.0 1.0
9522 0.08476901634187475 0.07432381037907616 1.0 1.0
9523 0.08476416889851777 0.0743205511329572 1.0 1.0
9524 0.08475932237623232 0.07431729207063895 1.0 1.0
9525 0.08475447677421015 0.07431403319306848 1.0 1.

9710 0.08387234713120828 0.07372022646046773 1.0 1.0
9711 0.08386765427012542 0.07371706913904644 1.0 1.0
9712 0.0838629622857721 0.073713911989821 1.0 1.0
9713 0.08385827117738723 0.07371075501369659 1.0 1.0
9714 0.08385358094421137 0.07370759821157552 1.0 1.0
9715 0.08384889158548701 0.07370444158435739 1.0 1.0
9716 0.0838442031004583 0.07370128513293907 1.0 1.0
9717 0.08383951548837122 0.07369812885821467 1.0 1.0
9718 0.08383482874847346 0.07369497276107542 1.0 1.0
9719 0.08383014191380452 0.07369182076922214 1.0 1.0
9720 0.08382545595607353 0.07368866894533864 1.0 1.0
9721 0.08382077087451582 0.07368551729033805 1.0 1.0
9722 0.08381608666836853 0.07368236580513043 1.0 1.0
9723 0.08381140333687051 0.0736792144906234 1.0 1.0
9724 0.08380672087926244 0.07367606334772149 1.0 1.0
9725 0.08380203929478684 0.07367291237732676 1.0 1.0
9726 0.08379735858268791 0.07366976158033833 1.0 1.0
9727 0.0837926787422117 0.07366661095765267 1.0 1.0
9728 0.08378799977260587 0.07366346051016347 1.0 1.0

9870 0.08313159350175654 0.07322128573742996 1.0 1.0
9871 0.08312702695140604 0.07321820571952337 1.0 1.0
9872 0.08312246047732907 0.07321513032229514 1.0 1.0
9873 0.08311789484284424 0.0732120550907327 1.0 1.0
9874 0.08311333004723219 0.07320898002569999 1.0 1.0
9875 0.08310876608977548 0.07320590512805834 1.0 1.0
9876 0.08310420296975818 0.07320283039866651 1.0 1.0
9877 0.08309964068646607 0.07319975583838066 1.0 1.0
9878 0.08309507923918658 0.07319668144805434 1.0 1.0
9879 0.08309051862720883 0.0731936111306315 1.0 1.0
9880 0.08308595787790438 0.07319054097355138 1.0 1.0
9881 0.08308139796862601 0.07318747097768916 1.0 1.0
9882 0.0830768388986506 0.0731844011439175 1.0 1.0
9883 0.0830722806672566 0.07318133147310625 1.0 1.0
9884 0.08306772327372418 0.07317826196612276 1.0 1.0
9885 0.0830631667173352 0.07317519262383172 1.0 1.0
9886 0.08305861099737313 0.07317212344709521 1.0 1.0
9887 0.0830540561131232 0.07316905443677267 1.0 1.0
9888 0.08304950200973146 0.07316598545677659 1.0 1.0


In [7]:
#Exercise 3:

#!/usr/bin/env python
# coding: utf-8

# In[2]:


#!/usr/bin/env python3
# -*- coding: utf-8 -*-
import pandas as pd;
from scipy.stats import zscore
import torch as torch;
import numpy as np;
from sklearn.model_selection import train_test_split
np.random.seed(42)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#read in the dataset, convert to numpy
dfData = pd.read_csv(r'C:\Users\Yoges\Desktop\Machine Learning\iris.csv')
np_x=dfData[list(dfData.columns)[0:-1]].apply(zscore).to_numpy();
np_y = pd.get_dummies(dfData['variety']).to_numpy();
n_classes = 3;

x_train, x_test, y_train, y_test = train_test_split(np_x, np_y, test_size=0.20, random_state=42)
n_features = x_train.shape[1];


# reshape training and testing data
# training data
x_train = x_train.astype(dtype='float64')
y_train = y_train.astype(dtype='float64')

# testing data
x_test = x_test.astype(dtype='float64')
y_test = y_test.astype(dtype='float64')

n_train = x_train.shape[0]

#define pytorch linear binary classifier
# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_train=torch.tensor(x_train,requires_grad=False,device=device);
t_y_train=torch.tensor(y_train,requires_grad=False,device=device);


t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);


#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)

# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.01;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)

batch_size=64;
n_epochs = 10000;

for i in range(n_epochs):    
    
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);
        
        # clear previous gradient calculations
        optimizer.zero_grad();
    
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );
    
    
        #calculate gradients of risk w.r.t. W,b and propagate them back
        risk.backward();
        # use the gradient to change W, b
        optimizer.step();
        
        batch_risk=risk.item();
        # calculate accuracy (on the training set!)
        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(activations.detach().cpu().numpy(),axis=1)
        accuracy = np.count_nonzero(true_class == pred_class)/pred_class.shape[0];
        error = 1.0 - accuracy;
        
    # after all the batches in this epoch are done, we calculate test set risk and accuracy
    with (torch.no_grad()):
            linear_predictions = torch.matmul(t_x_test,W)+b
            activations =  torch.exp(linear_predictions);
    
            #Passing through softmax
            sum_activations = torch.sum(activations,dim=1,keepdim=True)
            test_normalized_activations = torch.div(activations, sum_activations);
            cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
            test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
            test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
            test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
            test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
            test_error = 1.0 - test_accuracy;

    
    
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)
    
    #print (t_x_test.shape,test_normalized_activations.shape , t_y_test.shape)


0 1.0811321371602711 1.0505663287048297 0.5892857142857143 0.6333333333333333
1 1.031464932446716 0.9980707265273433 0.6071428571428571 0.6333333333333333
2 0.9852024458987919 0.9492932468699552 0.6071428571428571 0.6333333333333333
3 0.9422942699860987 0.9040620591030115 0.6071428571428571 0.6666666666666666
4 0.9025840993734422 0.8621892773100253 0.6428571428571429 0.8
5 0.8658567154933792 0.8234422137851326 0.8392857142857143 0.8666666666666667
6 0.8318631820250085 0.7875653229623398 0.8571428571428571 0.9
7 0.8003568678766702 0.7543179816203254 0.875 0.9333333333333333
8 0.7711218667065655 0.7234959205345969 0.8928571428571429 0.9333333333333333
9 0.7439826743303726 0.6949319290300051 0.875 0.9333333333333333
10 0.7187990691805568 0.6684857207473303 0.875 0.9333333333333333
11 0.6954550029713306 0.6440322192123796 0.8571428571428571 0.9333333333333333
12 0.6738475085150754 0.621452430935246 0.8392857142857143 0.9333333333333333
13 0.6538780717078689 0.6006277575674943 0.85714285714

126 0.2371498882426007 0.19273009647073688 0.9821428571428571 1.0
127 0.23595623582980355 0.19171504877893258 0.9821428571428571 1.0
128 0.23477378272149257 0.19071119348625215 0.9821428571428571 1.0
129 0.23360238238528977 0.18971837058955335 0.9821428571428571 1.0
130 0.23244188885731049 0.18873642091428955 0.9821428571428571 1.0
131 0.23129216098033376 0.18776519147356546 0.9821428571428571 1.0
132 0.23015305914341727 0.18680452850743065 0.9821428571428571 1.0
133 0.22902444778326708 0.18585428158114017 0.9821428571428571 1.0
134 0.2279061916373107 0.18491430430643846 0.9821428571428571 1.0
135 0.22679815997367472 0.18398445024845766 0.9821428571428571 1.0
136 0.22570022233891868 0.18306457764384654 0.9821428571428571 1.0
137 0.2246122515360755 0.18215454396523453 0.9821428571428571 1.0
138 0.22353412216735943 0.18125421433591576 0.9821428571428571 1.0
139 0.2224657114906006 0.1803634493261592 0.9821428571428571 1.0
140 0.22140689900157653 0.17948211613927764 0.9821428571428571 1.0


322 0.11796859102042201 0.10026519036097059 1.0 1.0
323 0.11766971920777365 0.10005269937500305 1.0 1.0
324 0.11737243221665435 0.09984138378182789 1.0 1.0
325 0.11707672095060273 0.0996312265266918 1.0 1.0
326 0.11678257407047644 0.09942222503276626 1.0 1.0
327 0.11648997820247041 0.09921436585610265 1.0 1.0
328 0.11619891891334401 0.0990076456630052 1.0 1.0
329 0.11590938630194027 0.09880204786023404 1.0 1.0
330 0.11562137071423186 0.09859756515354332 1.0 1.0
331 0.11533485747952628 0.09839418869204196 1.0 1.0
332 0.11504983710841858 0.09819190612417776 1.0 1.0
333 0.11476629946395756 0.09799071160346715 1.0 1.0
334 0.11448422978565334 0.0977905952369486 1.0 1.0
335 0.11420361886618502 0.09759154698073919 1.0 1.0
336 0.11392445636331192 0.09739355839321293 1.0 1.0
337 0.11364672956490769 0.09719661757866277 1.0 1.0
338 0.11337043094765245 0.09700072127655188 1.0 1.0
339 0.1130955473174532 0.09680585798620775 1.0 1.0
340 0.11282206827213903 0.09661201719068056 1.0 1.0
341 0.1125499853

506 0.08111373624245447 0.07406936838356866 0.9821428571428571 1.0
507 0.08098057851581565 0.07397298224862622 0.9821428571428571 1.0
508 0.08084790665313449 0.07387691366102388 0.9821428571428571 1.0
509 0.08071571787912638 0.07378116605873951 0.9821428571428571 1.0
510 0.08058400934872108 0.07368573345203577 0.9821428571428571 1.0
511 0.08045277692274379 0.07359062246763441 0.9821428571428571 1.0
512 0.08032201753269877 0.07349582581639728 0.9821428571428571 1.0
513 0.08019173190970146 0.07340133960032165 0.9821428571428571 1.0
514 0.08006191559351643 0.07330716710504523 0.9821428571428571 1.0
515 0.07993256731603104 0.0732132986811269 0.9821428571428571 1.0
516 0.07980368470415292 0.07311973647227872 0.9821428571428571 1.0
517 0.0796752634886614 0.07302648055334705 0.9821428571428571 1.0
518 0.07954730230936592 0.0729335280554483 0.9821428571428571 1.0
519 0.07941979888141147 0.07284087776887996 0.9821428571428571 1.0
520 0.0792927506465391 0.07274852825213354 0.9821428571428571 1.0

646 0.06625239218563006 0.06305480488755187 0.9821428571428571 1.0
647 0.06616809004774746 0.06299036366726958 0.9821428571428571 1.0
648 0.06608403499813427 0.06292608305838787 0.9821428571428571 1.0
649 0.06600022424915929 0.06286196061549146 0.9821428571428571 1.0
650 0.06591665824066968 0.06279799584730475 0.9821428571428571 1.0
651 0.06583333580164427 0.06273419022874628 0.9821428571428571 1.0
652 0.06575025413264382 0.06267054122762429 0.9821428571428571 1.0
653 0.06566741372855275 0.06260704832296728 0.9821428571428571 1.0
654 0.06558481341618436 0.06254371376691342 0.9821428571428571 1.0
655 0.06550245074727588 0.062480536226256385 0.9821428571428571 1.0
656 0.06542032437093566 0.06241751309931625 0.9821428571428571 1.0
657 0.06533843481124213 0.06235464369837133 0.9821428571428571 1.0
658 0.06525678098721961 0.06229192727909067 0.9821428571428571 1.0
659 0.06517536338795822 0.06222936145401013 0.9821428571428571 1.0
660 0.06509417931419752 0.06216694754354701 0.982142857142857

...

9179 0.014575483262129638 0.014188922764017481 1.0 1.0
9180 0.014575421714808154 0.014188861737962884 1.0 1.0
9181 0.01457536025113006 0.014188801247564487 1.0 1.0
9182 0.014575298875271167 0.01418874102382086 1.0 1.0
9183 0.014575237595166145 0.014188680799599384 1.0 1.0
9184 0.014575176416794068 0.01418862039119226 1.0 1.0
9185 0.014575115340375136 0.01418855973769829 1.0 1.0
9186 0.014575054359412797 0.0141884988926402 1.0 1.0
9187 0.014574993462363751 0.01418843797962262 1.0 1.0
9188 0.01457493263587371 0.014188377133693938 1.0 1.0
9189 0.014574871868092207 0.014188316451185219 1.0 1.0
9190 0.01457480847060731 0.014188250892450571 1.0 1.0
9191 0.014574745232281685 0.014188183699876749 1.0 1.0
9192 0.014574682247126868 0.01418811455191925 1.0 1.0
9193 0.014574619542108657 0.014188044010984032 1.0 1.0
9194 0.014574557088740725 0.014187973209887296 1.0 1.0
9195 0.014574494829269032 0.01418790338864406 1.0 1.0
9196 0.014574432706035107 0.014187835470019202 1.0 1.0
9197 0.01457437068366

9351 0.014565384075016482 0.014178481974339723 1.0 1.0
9352 0.014565327247337488 0.014178420943535032 1.0 1.0
9353 0.014565270624856921 0.014178360180603066 1.0 1.0
9354 0.014565214239213359 0.014178299567743583 1.0 1.0
9355 0.014565158102642506 0.014178239187914977 1.0 1.0
9356 0.014565102210343222 0.014178179267382183 1.0 1.0
9357 0.014565046546765738 0.014178120072877129 1.0 1.0
9358 0.014564991093193312 0.014178061808346581 1.0 1.0
9359 0.01456493583402108 0.014178004547760992 1.0 1.0
9360 0.014564880760045612 0.014177948221175405 1.0 1.0
9361 0.014564825868386812 0.014177892649769172 1.0 1.0
9362 0.014564771159857135 0.01417783760964954 1.0 1.0
9363 0.014564716635280112 0.014177782898146224 1.0 1.0
9364 0.014564662292312871 0.014177728380332415 1.0 1.0
9365 0.014564608123841418 0.014177674004309615 1.0 1.0
9366 0.014564554118264673 0.014177619786436663 1.0 1.0
9367 0.014564500261268095 0.014177565777533922 1.0 1.0
9368 0.014564446538245526 0.01417751202534034 1.0 1.0
9369 0.014564

9541 0.014555601637750036 0.014168403444700389 1.0 1.0
9542 0.01455555260026661 0.014168347869071974 1.0 1.0
9543 0.014555503681752166 0.01416829439067707 1.0 1.0
9544 0.014555454860366737 0.014168243073335017 1.0 1.0
9545 0.014555406144794836 0.014168193484210742 1.0 1.0
9546 0.01455535756487455 0.014168144922277475 1.0 1.0
9547 0.014555309156203526 0.014168096689615276 1.0 1.0
9548 0.014555260945215665 0.014168048307312128 1.0 1.0
9549 0.014555212939807 0.014167999614913 1.0 1.0
9550 0.014555165127732273 0.014167950743034211 1.0 1.0
9551 0.014555117481934646 0.014167901993289954 1.0 1.0
9552 0.014555069969777887 0.014167853684242924 1.0 1.0
9553 0.014555022562397655 0.014167806022215224 1.0 1.0
9554 0.014554975241051189 0.014167759036092227 1.0 1.0
9555 0.014554927998937253 0.014167712586130914 1.0 1.0
9556 0.01455488083876214 0.014167666429849115 1.0 1.0
9557 0.014554833767699605 0.014167620311974652 1.0 1.0
9558 0.014554786791948536 0.014167574043538446 1.0 1.0
9559 0.0145547399128

9722 0.014547444074735832 0.014160023120681481 1.0 1.0
9723 0.014547400454749523 0.014159971149151612 1.0 1.0
9724 0.014547356985039454 0.01415992016066554 1.0 1.0
9725 0.01454731360967433 0.014159871057127942 1.0 1.0
9726 0.014547270295654757 0.014159824181058368 1.0 1.0
9727 0.014547227041524795 0.014159779305978216 1.0 1.0
9728 0.014547183872694306 0.014159735812228654 1.0 1.0
9729 0.01454714082777325 0.014159692955729757 1.0 1.0
9730 0.01454709794239128 0.014159650123504394 1.0 1.0
9731 0.014547055236563067 0.014159606994205303 1.0 1.0
9732 0.014547012709278936 0.014159563569240818 1.0 1.0
9733 0.014546970340962287 0.014159520089413633 1.0 1.0
9734 0.014546928101415639 0.014159476887829618 1.0 1.0
9735 0.014546885959786817 0.014159434240900513 1.0 1.0
9736 0.014546843892844453 0.014159392268080141 1.0 1.0
9737 0.014546801889094291 0.01415935090518955 1.0 1.0
9738 0.014546759948345688 0.014159309946175766 1.0 1.0
9739 0.014546718077613123 0.014159264680772766 1.0 1.0
9740 0.01454667

9905 0.014540153197252709 0.014152459752422198 1.0 1.0
9906 0.01454011591816374 0.014152422067497252 1.0 1.0
9907 0.014540078723387136 0.014152385026114295 1.0 1.0
9908 0.014540041603835058 0.01415234852809689 1.0 1.0
9909 0.014540004560262295 0.014152312360288759 1.0 1.0
9910 0.014539967598912398 0.014152276277825672 1.0 1.0
9911 0.01453993072630407 0.014152240082484597 1.0 1.0
9912 0.0145398939450626 0.0141522036724504 1.0 1.0
9913 0.014539857251986794 0.014152167052201492 1.0 1.0
9914 0.014539820638565447 0.014152130306619843 1.0 1.0
9915 0.014539784093298872 0.014152093554554462 1.0 1.0
9916 0.014539744930171657 0.014152051847498731 1.0 1.0
9917 0.01453970592621826 0.014152008561447446 1.0 1.0
9918 0.014539667170643868 0.014151963441649236 1.0 1.0
9919 0.01453963136314119 0.014151922093093922 1.0 1.0
9920 0.014539593016062141 0.014151877210258996 1.0 1.0
9921 0.014539554766190694 0.014151833525558237 1.0 1.0
9922 0.014539516626277003 0.014151791053852015 1.0 1.0
9923 0.014539478616

In [8]:
#Exercise 3:

#!/usr/bin/env python
# coding: utf-8

# In[2]:


#!/usr/bin/env python3
# -*- coding: utf-8 -*-
import pandas as pd;
from scipy.stats import zscore
import torch as torch;
import numpy as np;
from sklearn.model_selection import train_test_split
np.random.seed(42)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#read in the dataset, convert to numpy
dfData = pd.read_csv(r'C:\Users\Yoges\Desktop\Machine Learning\iris.csv')
np_x=dfData[list(dfData.columns)[0:-1]].apply(zscore).to_numpy();
np_y = pd.get_dummies(dfData['variety']).to_numpy();
n_classes = 3;

x_train, x_test, y_train, y_test = train_test_split(np_x, np_y, test_size=0.20, random_state=42)
n_features = x_train.shape[1];


# reshape training and testing data
# training data
x_train = x_train.astype(dtype='float64')
y_train = y_train.astype(dtype='float64')

# testing data
x_test = x_test.astype(dtype='float64')
y_test = y_test.astype(dtype='float64')

n_train = x_train.shape[0]

#define pytorch linear binary classifier
# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_train=torch.tensor(x_train,requires_grad=False,device=device);
t_y_train=torch.tensor(y_train,requires_grad=False,device=device);


t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);


#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)

# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.1;
optimizer = torch.optim.SGD([W,b],lr=learning_rate)
#optimizer = torch.optim.Adam([W,b],lr=learning_rate)

batch_size=120;
n_epochs = 10000;

for i in range(n_epochs):    
    
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);
        
        # clear previous gradient calculations
        optimizer.zero_grad();
    
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );
    
    
        #calculate gradients of risk w.r.t. W,b and propagate them back
        risk.backward();
        # use the gradient to change W, b
        optimizer.step();
        
        batch_risk=risk.item();
        # calculate accuracy (on the training set!)
        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(activations.detach().cpu().numpy(),axis=1)
        accuracy = np.count_nonzero(true_class == pred_class)/pred_class.shape[0];
        error = 1.0 - accuracy;
        
    # after all the batches in this epoch are done, we calculate test set risk and accuracy
    with (torch.no_grad()):
            linear_predictions = torch.matmul(t_x_test,W)+b
            activations =  torch.exp(linear_predictions);
    
            #Passing through softmax
            sum_activations = torch.sum(activations,dim=1,keepdim=True)
            test_normalized_activations = torch.div(activations, sum_activations);
            cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
            test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
            test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
            test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
            test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
            test_error = 1.0 - test_accuracy;

    
    
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)
    
    #print (t_x_test.shape,test_normalized_activations.shape , t_y_test.shape)


0 1.1050259658340726 1.0108311457429626 0.20833333333333334 0.8666666666666667
1 1.0138387236067228 0.9316748048417804 0.8166666666666667 0.8666666666666667
2 0.9387747318045746 0.8663255269382429 0.8166666666666667 0.8666666666666667
3 0.8768932573636982 0.8120249185995714 0.8083333333333333 0.8666666666666667
4 0.825610831000127 0.7665178432989553 0.8083333333333333 0.8666666666666667
5 0.7827769325020822 0.728010955260792 0.8083333333333333 0.8666666666666667
6 0.7466630927060772 0.6950998827613113 0.8083333333333333 0.8666666666666667
7 0.7159085756297272 0.6666920853738423 0.8083333333333333 0.8666666666666667
8 0.6894531278185532 0.6419380992277552 0.8166666666666667 0.8666666666666667
9 0.6664731248169572 0.620175212834154 0.8166666666666667 0.8666666666666667
10 0.6463275827431688 0.6008833654052805 0.8166666666666667 0.8666666666666667
11 0.6285151778139839 0.5836514399289385 0.8166666666666667 0.8666666666666667
12 0.6126411192691019 0.5681518018000342 0.8166666666666667 0.86

118 0.32362106392123663 0.2673814651442317 0.9083333333333333 0.9666666666666667
119 0.3227825792334944 0.26655478005405203 0.9083333333333333 0.9666666666666667
120 0.3219507629778094 0.2657359856133769 0.9083333333333333 0.9666666666666667
121 0.32112549737853685 0.2649249346252486 0.9083333333333333 0.9666666666666667
122 0.3203066681157818 0.26412148115549416 0.9083333333333333 0.9666666666666667
123 0.31949416124870356 0.2633254841522067 0.9083333333333333 0.9666666666666667
124 0.31868786710545666 0.2625368083013769 0.9083333333333333 0.9666666666666667
125 0.3178876812686144 0.26175532380069955 0.9083333333333333 0.9666666666666667
126 0.3170935040596687 0.2609808986263926 0.9083333333333333 0.9666666666666667
127 0.316305232431267 0.2602134098827492 0.9083333333333333 0.9666666666666667
128 0.31552277220638436 0.2594527334116068 0.9083333333333333 0.9666666666666667
129 0.3147460275404831 0.25869875361769556 0.9083333333333333 0.9666666666666667
130 0.313974910038687 0.25795135

234 0.2542842763210296 0.20309561735829848 0.925 0.9666666666666667
235 0.25384826507735464 0.2027132410486909 0.925 0.9666666666666667
236 0.2534141654250022 0.2023327562193499 0.925 0.9666666666666667
237 0.25298196455627653 0.20195415000208553 0.925 0.9666666666666667
238 0.25255165126519363 0.20157740413882855 0.925 0.9666666666666667
239 0.2521232099725816 0.20120250426574973 0.925 0.9666666666666667
240 0.25169662848622804 0.20082943625851105 0.925 0.9666666666666667
241 0.2512718939841195 0.20045818425074896 0.925 0.9666666666666667
242 0.25084899330978666 0.20008873447268324 0.925 0.9666666666666667
243 0.2504279140960443 0.19972107142729573 0.925 0.9666666666666667
244 0.2500086432497309 0.19935518355077544 0.925 0.9666666666666667
245 0.24959117027983005 0.19899105384476476 0.925 0.9666666666666667
246 0.24917548074321239 0.19862866921945935 0.925 0.9666666666666667
247 0.24876156295821916 0.1982680167199836 0.925 0.9666666666666667
248 0.2483494057450419 0.19790908170617025 

373 0.2076611878079887 0.16329734485491762 0.9416666666666667 1.0
374 0.20740374981509427 0.16308318730749513 0.9416666666666667 1.0
375 0.20714716360376167 0.16286979852219213 0.9416666666666667 1.0
376 0.20689142635214094 0.16265716949886702 0.9416666666666667 1.0
377 0.2066365306388613 0.1624453019922595 0.9416666666666667 1.0
378 0.20638247608578109 0.1622341870592164 0.9416666666666667 1.0
379 0.206129255343468 0.16202382456841272 0.9416666666666667 1.0
380 0.20587686712308167 0.16181420943851238 0.9416666666666667 1.0
381 0.20562530614491006 0.1616053362708398 0.9416666666666667 1.0
382 0.20537456763193376 0.16139720156369694 0.9416666666666667 1.0
383 0.2051246478749065 0.1611898018399921 0.9416666666666667 1.0
384 0.2048755431934929 0.16098313371840892 0.9416666666666667 1.0
385 0.20462724984013084 0.1607771937702561 0.9416666666666667 1.0
386 0.2043797641916377 0.160571975157603 0.9416666666666667 1.0
387 0.2041330801740782 0.1603674779498488 0.9416666666666667 1.0
388 0.20388

564 0.1702782619209899 0.1328168786936589 0.9583333333333334 1.0
565 0.17012996302988997 0.13269848102108914 0.9583333333333334 1.0
566 0.16998203676296714 0.13258040283323141 0.9583333333333334 1.0
567 0.16983448380623542 0.1324626432577495 0.9583333333333334 1.0
568 0.16968730279905977 0.132345201050555 0.9583333333333334 1.0
569 0.16954049257474785 0.13222807223065064 0.9583333333333334 1.0
570 0.16939404990493837 0.1321112588959331 0.9583333333333334 1.0
571 0.16924797540421277 0.13199475981250905 0.9583333333333334 1.0
572 0.16910226792863362 0.13187857101486794 0.9583333333333334 1.0
573 0.16895692428177064 0.1317626946067861 0.9583333333333334 1.0
574 0.16881194509403855 0.13164712295990935 0.9583333333333334 1.0
575 0.1686673255910715 0.13153185859220662 0.9583333333333334 1.0
576 0.16852306620991436 0.13141690361225464 0.9583333333333334 1.0
577 0.1683791675973508 0.13130225370182275 0.9583333333333334 1.0
578 0.16823562678950796 0.13118790806025168 0.9583333333333334 1.0
579 

...

9341 0.059233179091123446 0.0424269009144249 0.9833333333333333 1.0
9342 0.05923190216014773 0.04242528403813321 0.9833333333333333 1.0
9343 0.0592306254349216 0.04242366724454679 0.9833333333333333 1.0
9344 0.05922934891518836 0.042422050535701285 0.9833333333333333 1.0
9345 0.05922807260069279 0.04242043391361568 0.9833333333333333 1.0
9346 0.059226796491181455 0.042418820093716475 0.9833333333333333 1.0
9347 0.05922552127639074 0.04241720632915396 0.9833333333333333 1.0
9348 0.059224246269501284 0.04241559262218151 0.9833333333333333 1.0
9349 0.05922297147023723 0.04241397897503426 0.9833333333333333 1.0
9350 0.05922169687832452 0.042412365389929076 0.9833333333333333 1.0
9351 0.05922042249349085 0.04241075186906494 0.9833333333333333 1.0
9352 0.059219148315465625 0.04240913841462267 0.9833333333333333 1.0
9353 0.05921787434397999 0.042407525028765644 0.9833333333333333 1.0
9354 0.05921660057876677 0.04240591171363927 0.9833333333333333 1.0
9355 0.0592153270195605 0.0424042984713716

9519 0.05900966971208827 0.042142637523489936 0.9833333333333333 1.0
9520 0.05900843515999091 0.04214106009015395 0.9833333333333333 1.0
9521 0.05900720080358311 0.04213948273441313 0.9833333333333333 1.0
9522 0.05900596664262084 0.04213790545822612 0.9833333333333333 1.0
9523 0.059004732676861356 0.042136330916017935 0.9833333333333333 1.0
9524 0.05900349958468062 0.042134756422432924 0.9833333333333333 1.0
9525 0.05900226669056873 0.04213318197965996 0.9833333333333333 1.0
9526 0.059001033994261425 0.04213160758987001 0.9833333333333333 1.0
9527 0.058999801495496024 0.04213003325521657 0.9833333333333333 1.0
9528 0.058998569194011544 0.042128458977835785 0.9833333333333333 1.0
9529 0.058997337089548615 0.04212688475984653 0.9833333333333333 1.0
9530 0.05899610518184961 0.042125310603350404 0.9833333333333333 1.0
9531 0.05899487347065847 0.042123736510432205 0.9833333333333333 1.0
9532 0.05899364195572073 0.04212216248315966 0.9833333333333333 1.0
9533 0.058992410636783586 0.042120588

9658 0.0588402624676057 0.041925430620606385 0.9833333333333333 1.0
9659 0.058839059189163635 0.041923881402960134 0.9833333333333333 1.0
9660 0.05883785609692211 0.04192233228179287 0.9833333333333333 1.0
9661 0.05883665319066173 0.04192078325883613 0.9833333333333333 1.0
9662 0.058835450470164315 0.04191923433580735 0.9833333333333333 1.0
9663 0.05883424793521311 0.041917685514409914 0.9833333333333333 1.0
9664 0.05883304558559261 0.04191613679633339 0.9833333333333333 1.0
9665 0.05883184342108862 0.041914588183253484 0.9833333333333333 1.0
9666 0.058830641441488245 0.041913039676832034 0.9833333333333333 1.0
9667 0.058829439646579905 0.04191149127871754 0.9833333333333333 1.0
9668 0.058828238036153245 0.04190994299054487 0.9833333333333333 1.0
9669 0.058827036609999155 0.0419083996679043 0.9833333333333333 1.0
9670 0.058825836675121375 0.041906856387815106 0.9833333333333333 1.0
9671 0.058824636930773735 0.041905313152421506 0.9833333333333333 1.0
9672 0.05882343737670023 0.04190376

9799 0.0586728089545451 0.041709205808417006 0.9833333333333333 1.0
9800 0.05867163683656875 0.04170768685306561 0.9833333333333333 1.0
9801 0.05867046489942101 0.041706167972458276 0.9833333333333333 1.0
9802 0.058669293142878096 0.04170464916841263 0.9833333333333333 1.0
9803 0.05866812156671771 0.041703130442731565 0.9833333333333333 1.0
9804 0.05866695017071884 0.04170161179720354 0.9833333333333333 1.0
9805 0.05866577895466188 0.041700093233602464 0.9833333333333333 1.0
9806 0.05866460791832859 0.04169857475368799 0.9833333333333333 1.0
9807 0.058663437061502045 0.041697056359205426 0.9833333333333333 1.0
9808 0.058662266383966655 0.04169553805188612 0.9833333333333333 1.0
9809 0.058661095885508135 0.041694019833447296 0.9833333333333333 1.0
9810 0.058659925565913526 0.041692501705592196 0.9833333333333333 1.0
9811 0.05865875542497116 0.041690983670010326 0.9833333333333333 1.0
9812 0.058657585462470685 0.04168946572837762 0.9833333333333333 1.0
9813 0.05865641567820298 0.04168794

9932 0.058518754765191264 0.04150890778204843 0.9833333333333333 1.0
9933 0.05851761004541104 0.041507413501904504 0.9833333333333333 1.0
9934 0.05851646549740643 0.0415059193217517 0.9833333333333333 1.0
9935 0.058515321120981865 0.04150442775912945 0.9833333333333333 1.0
9936 0.05851417756955652 0.041502936266125556 0.9833333333333333 1.0
9937 0.058513034192500424 0.04150144484452653 0.9833333333333333 1.0
9938 0.058511890989596985 0.04149995349610474 0.9833333333333333 1.0
9939 0.058510747960630986 0.04149846222261795 0.9833333333333333 1.0
9940 0.058509605105388565 0.04149697102581005 0.9833333333333333 1.0
9941 0.05850846242365714 0.04149547990741072 0.9833333333333333 1.0
9942 0.058507319915225474 0.0414939888691358 0.9833333333333333 1.0
9943 0.058506177579883585 0.04149249791268727 0.9833333333333333 1.0
9944 0.05850503541742283 0.041491007039753294 0.9833333333333333 1.0
9945 0.05850389342763581 0.04148951841979036 0.9833333333333333 1.0
9946 0.05850275223208396 0.041488029851

In [9]:
#Exercise 3:

#!/usr/bin/env python
# coding: utf-8

# In[2]:


#!/usr/bin/env python3
# -*- coding: utf-8 -*-
import pandas as pd;
from scipy.stats import zscore
import torch as torch;
import numpy as np;
from sklearn.model_selection import train_test_split
np.random.seed(42)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#read in the dataset, convert to numpy
dfData = pd.read_csv(r'C:\Users\Yoges\Desktop\Machine Learning\iris.csv')
np_x=dfData[list(dfData.columns)[0:-1]].apply(zscore).to_numpy();
np_y = pd.get_dummies(dfData['variety']).to_numpy();
n_classes = 3;

x_train, x_test, y_train, y_test = train_test_split(np_x, np_y, test_size=0.20, random_state=42)
n_features = x_train.shape[1];


# reshape training and testing data
# training data
x_train = x_train.astype(dtype='float64')
y_train = y_train.astype(dtype='float64')

# testing data
x_test = x_test.astype(dtype='float64')
y_test = y_test.astype(dtype='float64')

n_train = x_train.shape[0]

#define pytorch linear binary classifier
# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_train=torch.tensor(x_train,requires_grad=False,device=device);
t_y_train=torch.tensor(y_train,requires_grad=False,device=device);


t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);


#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)

# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.1;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)

batch_size=120;
n_epochs = 10000;

for i in range(n_epochs):    
    
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);
        
        # clear previous gradient calculations
        optimizer.zero_grad();
    
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );
    
    
        #calculate gradients of risk w.r.t. W,b and propagate them back
        risk.backward();
        # use the gradient to change W, b
        optimizer.step();
        
        batch_risk=risk.item();
        # calculate accuracy (on the training set!)
        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(activations.detach().cpu().numpy(),axis=1)
        accuracy = np.count_nonzero(true_class == pred_class)/pred_class.shape[0];
        error = 1.0 - accuracy;
        
    # after all the batches in this epoch are done, we calculate test set risk and accuracy
    with (torch.no_grad()):
            linear_predictions = torch.matmul(t_x_test,W)+b
            activations =  torch.exp(linear_predictions);
    
            #Passing through softmax
            sum_activations = torch.sum(activations,dim=1,keepdim=True)
            test_normalized_activations = torch.div(activations, sum_activations);
            cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
            test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
            test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
            test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
            test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
            test_error = 1.0 - test_accuracy;

    
    
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)
    
    #print (t_x_test.shape,test_normalized_activations.shape , t_y_test.shape)


0 1.1050259658340726 0.8687183999872023 0.20833333333333334 0.6333333333333333
1 0.8619966474947743 0.6962019706900321 0.6666666666666666 0.7666666666666667
2 0.6987596363251979 0.5711055675120653 0.775 0.9333333333333333
3 0.5861637446616847 0.48231898722764466 0.85 0.9
4 0.5084104167740155 0.41965649143728967 0.8333333333333334 0.9
5 0.4548748075901418 0.3730407374508411 0.8333333333333334 0.9
6 0.4164463920076969 0.3362324322988261 0.8166666666666667 0.9333333333333333
7 0.38740536964053723 0.30627356058039 0.85 0.9333333333333333
8 0.3646353409740127 0.28177381787891065 0.8666666666666667 0.9333333333333333
9 0.34634036771856086 0.26175891976164883 0.85 0.9333333333333333
10 0.3311935555232782 0.24524175325166844 0.85 0.9333333333333333
11 0.31803047142646673 0.23124980752442856 0.8416666666666667 0.9666666666666667
12 0.3058609599045443 0.21901083862585966 0.85 0.9666666666666667
13 0.2939858286415062 0.2080868022939392 0.8666666666666667 0.9666666666666667
14 0.282086569359722 0.

117 0.08047137494970522 0.06708292176836408 0.9666666666666667 0.9666666666666667
118 0.08017155318692644 0.06681917882315448 0.9666666666666667 0.9666666666666667
119 0.07987609800071864 0.06655642675231369 0.975 0.9666666666666667
120 0.07958491516312419 0.06629436907006908 0.975 0.9666666666666667
121 0.07929791242360018 0.06603290653076473 0.975 0.9666666666666667
122 0.0790150005195964 0.0657721344490656 0.975 0.9666666666666667
123 0.07873609436255687 0.06551230266055036 0.975 0.9666666666666667
124 0.07846111221781345 0.0652537714610162 0.975 0.9666666666666667
125 0.07818997560099991 0.06499695618036833 0.975 0.9666666666666667
126 0.07792260888936094 0.06474225764060369 0.975 0.9666666666666667
127 0.07765893754725242 0.06449002115858446 0.975 0.9666666666666667
128 0.07739888900580745 0.06424048604143953 0.975 0.9666666666666667
129 0.07714239174769016 0.0639937758861089 0.975 0.9666666666666667
130 0.07688937653977804 0.06374989103545359 0.975 0.9666666666666667
131 0.076639

263 0.059601142844607366 0.04389512387235084 0.9833333333333333 1.0
264 0.05953567177833793 0.04380232847385583 0.9833333333333333 1.0
265 0.059470700960708514 0.043710042597106584 0.9833333333333333 1.0
266 0.05940622487685542 0.043618261753453416 0.9833333333333333 1.0
267 0.05934223828560811 0.04352698296712028 0.9833333333333333 1.0
268 0.059278736014496174 0.0434362006545193 0.9833333333333333 1.0
269 0.0592157127696576 0.043345910095991654 0.9833333333333333 1.0
270 0.0591531633268975 0.043256107130012066 0.9833333333333333 1.0
271 0.05909108272573214 0.04316678915599721 0.9833333333333333 1.0
272 0.05902946606865485 0.04307795095984908 0.9833333333333333 1.0
273 0.058968308334862725 0.04298958823671448 0.9833333333333333 1.0
274 0.058907604567919616 0.042901698917210664 0.9833333333333333 1.0
275 0.05884735026224971 0.042814278719027626 0.9833333333333333 1.0
276 0.058787540593312954 0.04272732260952271 0.9833333333333333 1.0
277 0.05872817080720637 0.0426408274111109 0.98333333

387 0.05412147463084853 0.03528973939969351 0.9833333333333333 1.0
388 0.05409211037333404 0.03523806171497888 0.9833333333333333 1.0
389 0.05406290734069201 0.03518659446220117 0.9833333333333333 1.0
390 0.05403386419790013 0.03513533639123152 0.9833333333333333 1.0
391 0.05400497974359276 0.03508428626680529 0.9833333333333333 1.0
392 0.05397625278605854 0.03503344258495229 0.9833333333333333 1.0
393 0.0539476820217512 0.03498280466014811 0.9833333333333333 1.0
394 0.05391926639838198 0.03493237135087746 0.9833333333333333 1.0
395 0.053891004756171056 0.03488214124654895 0.9833333333333333 1.0
396 0.05386289570890902 0.03483211352810087 0.9833333333333333 1.0
397 0.053834938359590474 0.03478228662405756 0.9833333333333333 1.0
398 0.05380713146609687 0.03473265979195095 0.9833333333333333 1.0
399 0.05377947392190847 0.03468323123858833 0.9833333333333333 1.0
400 0.0537519646343051 0.034633999750497066 0.9833333333333333 1.0
401 0.053724602405115326 0.0345849641023852 0.983333333333333

529 0.0511378510795132 0.02959317143884145 0.9833333333333333 1.0
530 0.05112303258508259 0.029562148843672423 0.9833333333333333 1.0
531 0.05110827704538605 0.02953122385749456 0.9833333333333333 1.0
532 0.051093584182887786 0.02950039728408459 0.9833333333333333 1.0
533 0.051078953488461164 0.029469668670042058 0.9833333333333333 1.0
534 0.05106438461201858 0.02943903675388716 0.9833333333333333 1.0
535 0.05104987728128565 0.029408501468910202 0.9833333333333333 1.0
536 0.05103543114967857 0.029378061926519945 0.9833333333333333 1.0
537 0.05102104587738807 0.029347718405800798 0.9833333333333333 1.0
538 0.05100672105192158 0.029317469470885094 0.9833333333333333 1.0
539 0.05099245641981777 0.029287315399287712 0.9833333333333333 1.0
540 0.050978251575542456 0.029257255595473004 0.9833333333333333 1.0
541 0.0509641061928743 0.02922728955841079 0.9833333333333333 1.0
542 0.050950019945532055 0.029197416780060555 0.9833333333333333 1.0
543 0.050935992507836744 0.029167636819685115 0.983

...

9376 0.046579045380300756 0.015322637227160976 0.9833333333333333 1.0
9377 0.04657904503291503 0.015321208770812283 0.9833333333333333 1.0
9378 0.046579044764562094 0.015322948770074285 0.9833333333333333 1.0
9379 0.046579044620199905 0.015320810464763352 0.9833333333333333 1.0
9380 0.046579044670836366 0.015323436415046698 0.9833333333333333 1.0
9381 0.04657904502026344 0.015320186520188676 0.9833333333333333 1.0
9382 0.046579045840812315 0.015324214566267027 0.9833333333333333 1.0
9383 0.04657904740580562 0.01531920208330466 0.9833333333333333 1.0
9384 0.04657905016854326 0.015325474174736472 0.9833333333333333 1.0
9385 0.04657905485583948 0.015317616176183926 0.9833333333333333 1.0
9386 0.04657906267286107 0.015327529075766488 0.9833333333333333 1.0
9387 0.04657907554074646 0.015315031513059758 0.9833333333333333 1.0
9388 0.04657909673655693 0.015330926762568385 0.9833333333333333 1.0
9389 0.0465791315295371 0.015310787065562268 0.9833333333333333 1.0
9390 0.046579189154131326 0.015

9506 0.04657898267186707 0.015322462685038373 0.9833333333333333 1.0
9507 0.04657898272323435 0.015320770872808913 0.9833333333333333 1.0
9508 0.04657898279842145 0.015322699809249225 0.9833333333333333 1.0
9509 0.046578982442843996 0.015320759182450084 0.9833333333333333 1.0
9510 0.046578981614718254 0.015322136468675834 0.9833333333333333 1.0
9511 0.046578980626309406 0.015321471969898161 0.9833333333333333 1.0
9512 0.04657897984188685 0.015321434640164723 0.9833333333333333 1.0
9513 0.04657897941374622 0.015322207466431084 0.9833333333333333 1.0
9514 0.04657897921939187 0.015320948813638801 0.9833333333333333 1.0
9515 0.04657897900171741 0.015322306560100795 0.9833333333333333 1.0
9516 0.04657897857276315 0.015320941568506578 0.9833333333333333 1.0
9517 0.04657897792746841 0.015321921261844531 0.9833333333333333 1.0
9518 0.046578977210014735 0.015321448403079226 0.9833333333333333 1.0
9519 0.04657897658799882 0.015321455466990732 0.9833333333333333 1.0
9520 0.04657897613376274 0.015

9627 0.04657892764479029 0.01532138115634228 0.9833333333333333 1.0
9628 0.04657892720170173 0.01532128037007724 0.9833333333333333 1.0
9629 0.046578926758949014 0.015321390881026891 0.9833333333333333 1.0
9630 0.04657892631678181 0.015321262241818167 0.9833333333333333 1.0
9631 0.04657892587526803 0.015321406983076907 0.9833333333333333 1.0
9632 0.04657892543435106 0.015321236434801506 0.9833333333333333 1.0
9633 0.04657892499401515 0.015321427205283119 0.9833333333333333 1.0
9634 0.046578924554606695 0.01532120238002208 0.9833333333333333 1.0
9635 0.046578924116534935 0.015321455035026464 0.9833333333333333 1.0
9636 0.04657892367995099 0.015321159674502085 0.9833333333333333 1.0
9637 0.046578923245167374 0.015321495087772608 0.9833333333333333 1.0
9638 0.046578922812752825 0.015321108659117282 0.9833333333333333 1.0
9639 0.0465789223832574 0.015321551612849489 0.9833333333333333 1.0
9640 0.04657892195837643 0.015321034126321773 0.9833333333333333 1.0
9641 0.046578921541213535 0.01532

9747 0.046578886354858885 0.015316833128490562 0.9833333333333333 1.0
9748 0.04657889826679536 0.015326033241158669 0.9833333333333333 1.0
9749 0.04657890055473015 0.015317783407383394 0.9833333333333333 1.0
9750 0.04657889166647348 0.015323405247487524 0.9833333333333333 1.0
9751 0.046578879876309244 0.015321020559682213 0.9833333333333333 1.0
9752 0.04657887440168777 0.015319325415017087 0.9833333333333333 1.0
9753 0.0465788774451807 0.01532409556879409 0.9833333333333333 1.0
9754 0.04657888378698501 0.015318012075793227 0.9833333333333333 1.0
9755 0.046578886601109135 0.015324495498153868 0.9833333333333333 1.0
9756 0.04657888333880062 0.015319471342466133 0.9833333333333333 1.0
9757 0.046578876959845715 0.015321870512930859 0.9833333333333333 1.0
9758 0.046578872379419815 0.015321819241597468 0.9833333333333333 1.0
9759 0.04657887216198404 0.015319264491065894 0.9833333333333333 1.0
9760 0.04657887494124259 0.015323562828777238 0.9833333333333333 1.0
9761 0.046578877308028704 0.015

9872 0.046578826122617586 0.015320800455817497 0.9833333333333333 1.0
9873 0.046578825729595714 0.01532079386456699 0.9833333333333333 1.0
9874 0.04657882533676893 0.015320810256123784 0.9833333333333333 1.0
9875 0.04657882494410886 0.015320787629060518 0.9833333333333333 1.0
9876 0.046578824551655726 0.015320815044647818 0.9833333333333333 1.0
9877 0.046578824159355006 0.015320772976478776 0.9833333333333333 1.0
9878 0.04657882376725461 0.015320813987054767 0.9833333333333333 1.0
9879 0.046578823375329224 0.015320759080802243 0.9833333333333333 1.0
9880 0.04657882298355687 0.015320816487161718 0.9833333333333333 1.0
9881 0.0465788225919247 0.015320753230429935 0.9833333333333333 1.0
9882 0.046578822200448435 0.015320824093458344 0.9833333333333333 1.0
9883 0.04657882180918617 0.015320746240430786 0.9833333333333333 1.0
9884 0.04657882141821692 0.015320829872492947 0.9833333333333333 1.0
9885 0.0465788210274416 0.015320732578011607 0.9833333333333333 1.0
9886 0.04657882063684926 0.0153